In [13]:
import numpy as np
import pandas as pd
import csv

from scipy.spatial.distance import cdist

from pymoo.algorithms.moo.nsga3 import NSGA3
from pymoo.algorithms.moo.nsga2 import NSGA2


from pymoo.operators.selection.tournament import TournamentSelection
from pymoo.algorithms.moo.nsga2 import binary_tournament
from pymoo.algorithms.moo.nsga3 import comp_by_cv_then_random

from pymoo.core.problem import ElementwiseProblem

from pymoo.operators.sampling.rnd import PermutationRandomSampling
from pymoo.operators.crossover.ox import OrderCrossover
from pymoo.operators.mutation.inversion import InversionMutation

from pymoo.util.display.column import Column
from pymoo.util.display.output import Output
from pymoo.util.display.display import Display

from pymoo.optimize import minimize
from pymoo.util.ref_dirs import get_reference_directions

import csv
import time

In [14]:
kroA100=pd.read_csv('C:/Users/Maria/Documents/Python Scripts/kroA100.csv', header=0, encoding='utf-8', skip_blank_lines=False, delimiter=r",")
kroB100=pd.read_csv('C:/Users/Maria/Documents/Python Scripts/kroB100.csv', header=0, encoding='utf-8', skip_blank_lines=False, delimiter=r",")
kroC100=pd.read_csv('C:/Users/Maria/Documents/Python Scripts/kroC100.csv', header=0, encoding='utf-8', skip_blank_lines=False, delimiter=r",")

In [15]:
class measure_time(Output):
    def __init__(self):
        super().__init__()
        self.x_time = Column("x_time", width=13)
        self.columns += [self.x_time]

    def update(self, algorithm):
        super().update(algorithm)
        writer.writerow([time.time() - start_time])
        self.x_time.set(time.time() - start_time)

In [16]:
class TravelingSalesman(ElementwiseProblem):
    def __init__(self, cost_one, cost_two, cost_three, **kwargs):
        n_one, _   = cost_one.shape

        self.one = cost_one
        self.two = cost_two
        self.three = cost_three
        
        super().__init__(n_var=n_one, n_obj=3, xl=0, xu=n_one, vtype=int, **kwargs)

    def _evaluate(self, x, out, *args, **kwargs):
        out['F'] = self.get_route_length(x)

    def get_route_length(self, x):
        n_cities = len(x)
        dist_one = 0
        dist_two = 0
        dist_three = 0
        
        for k in range(n_cities - 1):
            i, j = x[k], x[k + 1]
            dist_one += self.one[i, j]
            dist_two += self.two[i, j]
            dist_three += self.three[i, j]

        last, first = x[-1], x[0]
        
        dist_one += self.one[last, first]
        dist_one = 100000/dist_one
        dist_two += self.two[last, first]
        dist_two = 100000/dist_two
        dist_three += self.three[last, first]
        dist_three = 100000/dist_three
        
        return dist_one, dist_two, dist_three

In [17]:
cost_one = kroA100.values
cost_two = kroB100.values
cost_three = kroC100.values

one = cdist(cost_one,cost_one)
two = cdist(cost_two,cost_two)
three = cdist(cost_three,cost_three)

In [18]:
problem = TravelingSalesman(cost_one=one, cost_two=two, cost_three=three)

In [19]:
ref_dirs = get_reference_directions("das-dennis", 3, n_partitions=12)

In [20]:
algorithm_nsga3 = NSGA3(pop_size=92,
                        sampling=PermutationRandomSampling(),
                        selection=TournamentSelection(func_comp=comp_by_cv_then_random),
                        crossover=OrderCrossover(),
                        mutation=InversionMutation(),
                        ref_dirs=ref_dirs,
                        eliminate_duplicates=False)

In [21]:
algorithm_nsga2 = NSGA2(pop_size=92,
                        sampling=PermutationRandomSampling(),
                        selection=TournamentSelection(func_comp=binary_tournament),
                        crossover=OrderCrossover(),
                        mutation=InversionMutation(),
                        eliminate_duplicates=False)

In [ ]:
with open('pymoo_time_nsga2_motsp_92_500_3_100.csv', 'w', newline='') as f, open('pymoo_fitness_nsga2_motsp_92_500_3_100.csv','w', newline='') as g:
    writer = csv.writer(f)
    writer.writerow(["Execution Time"])
    
    writerFitness = csv.writer(g)
    writer.writerow(["f1","f2","f3"])
    start_time = time.time()
    res_motsp_nsga2 = minimize(problem, algorithm_nsga2, ('n_gen', 5000), output=measure_time(), verbose=True, save_history=False, seed=1)    
    for fitness in res_motsp_nsga2.F:
            writerFitness.writerow(fitness)

In [ ]:
with open('pymoo_time_nsga3_motsp_92_500_3_100.csv', 'w', newline='') as f, open('pymoo_fitness_nsga3_motsp_92_500_3_100.csv','w', newline='') as g:
    writer = csv.writer(f)
    writer.writerow(["Execution Time"])
    
    writerFitness = csv.writer(g)
    writer.writerow(["f1","f2","f3"])
    start_time = time.time()
    res_motsp_nsga3 = minimize(problem, algorithm_nsga3, ('n_gen', 5000), output=measure_time(), verbose=True, save_history=False, seed=1)
    for fitness in res_motsp_nsga3.F:
            writerFitness.writerow(fitness)

In [ ]:
with open('pymoo_pop_nsga3_motsp_91_500_3_100.csv', 'w', newline='') as f, open('pymoo_fitness_nsga3_motsp_91_500_3_100.csv','w', newline='') as g:
    writer = csv.writer(f)    
    writerFitness = csv.writer(g)
    writer.writerow(["f1","f2","f3"])
    
    for fitness in res_motsp_nsga3.F:
            writerFitness.writerow(fitness)
            
    for pop in res_motsp_nsga3.X:
            writer.writerow(pop)

In [ ]:
with open('pymoo_pop_nsga2_motsp_92_500_3_100.csv', 'w', newline='') as f, open('pymoo_fitness_nsga2_motsp_92_500_3_100.csv','w', newline='') as g:
    writer = csv.writer(f)    
    writerFitness = csv.writer(g)
    writer.writerow(["f1","f2","f3"])
    
    for fitness in res_motsp_nsga2.F:
            writerFitness.writerow(fitness)
            
    for pop in res_motsp_nsga2.X:
            writer.writerow(pop)

In [22]:
for i in range(1, 11):
    print(f"Iteration {i}")

    with open(f'pymoo_time_nsga2_motsp_92_500_3_100-{i}.csv', 'w', newline='') as f, open(f'pymoo_fitness_nsga2_motsp_92_500_3_100-{i}.csv','w', newline='') as g:
        writer = csv.writer(f)
        writer.writerow(["Execution Time"])

        writerFitness = csv.writer(g)
        writer.writerow(["f1","f2","f3"])
        start_time = time.time()
        res_motsp_nsga2 = minimize(problem, algorithm_nsga2, ('n_gen', 5000), seed=i, output=measure_time(), verbose=True, save_history=False)    
        for fitness in res_motsp_nsga2.F:
                writerFitness.writerow(fitness)

    with open(f'pymoo_time_nsga3_motsp_92_500_3_100-{i}.csv', 'w', newline='') as f, open(f'pymoo_fitness_nsga3_motsp_92_500_3_100-{i}.csv','w', newline='') as g:
        writer = csv.writer(f)
        writer.writerow(["Execution Time"])

        writerFitness = csv.writer(g)
        writer.writerow(["f1","f2","f3"])
        start_time = time.time()
        res_motsp_nsga3 = minimize(problem, algorithm_nsga3, ('n_gen', 5000), seed=i, output=measure_time(), verbose=True, save_history=False)
        for fitness in res_motsp_nsga3.F:
                writerFitness.writerow(fitness)


Iteration 1
n_gen  |  n_eval  |     x_time   
     1 |       92 |  0.1011283398
     2 |      184 |  0.1411368847
     3 |      276 |  0.2162840366
     4 |      368 |  0.2560622692
     5 |      460 |  0.2812199593
     6 |      552 |  0.3209841251
     7 |      644 |  0.3612413406
     8 |      736 |  0.4009740353
     9 |      828 |  0.4397988319
    10 |      920 |  0.4927864075
    11 |     1012 |  0.5259516239
    12 |     1104 |  0.5659203529
    13 |     1196 |  0.6457581520
    14 |     1288 |  0.6985247135
    15 |     1380 |  0.7408685684
    16 |     1472 |  0.7809915543
    17 |     1564 |  0.8217921257
    18 |     1656 |  0.8669376373
    19 |     1748 |  0.9056391716
    20 |     1840 |  0.9581692219
    21 |     1932 |  1.0010738373
    22 |     2024 |  1.0608985424
    23 |     2116 |  1.1010012627
    24 |     2208 |  1.1509048939
    25 |     2300 |  1.2033863068
    26 |     2392 |  1.2391738892
    27 |     2484 |  1.2846148014
    28 |     2576 |  1.3470523357
  

   240 |    22080 |  1.068101E+01
   241 |    22172 |  1.075098E+01
   242 |    22264 |  1.080099E+01
   243 |    22356 |  1.085109E+01
   244 |    22448 |  1.091631E+01
   245 |    22540 |  1.096114E+01
   246 |    22632 |  1.100083E+01
   247 |    22724 |  1.104083E+01
   248 |    22816 |  1.107108E+01
   249 |    22908 |  1.112087E+01
   250 |    23000 |  1.117599E+01
   251 |    23092 |  1.122089E+01
   252 |    23184 |  1.132933E+01
   253 |    23276 |  1.138086E+01
   254 |    23368 |  1.145347E+01
   255 |    23460 |  1.151804E+01
   256 |    23552 |  1.156378E+01
   257 |    23644 |  1.160767E+01
   258 |    23736 |  1.165464E+01
   259 |    23828 |  1.169986E+01
   260 |    23920 |  1.174094E+01
   261 |    24012 |  1.178368E+01
   262 |    24104 |  1.182861E+01
   263 |    24196 |  1.188103E+01
   264 |    24288 |  1.193869E+01
   265 |    24380 |  1.200084E+01
   266 |    24472 |  1.206277E+01
   267 |    24564 |  1.210097E+01
   268 |    24656 |  1.215555E+01
   269 |    24

   481 |    44252 |  2.261083E+01
   482 |    44344 |  2.265123E+01
   483 |    44436 |  2.269095E+01
   484 |    44528 |  2.275105E+01
   485 |    44620 |  2.280109E+01
   486 |    44712 |  2.285087E+01
   487 |    44804 |  2.289582E+01
   488 |    44896 |  2.293091E+01
   489 |    44988 |  2.297078E+01
   490 |    45080 |  2.301887E+01
   491 |    45172 |  2.305086E+01
   492 |    45264 |  2.309081E+01
   493 |    45356 |  2.312086E+01
   494 |    45448 |  2.316573E+01
   495 |    45540 |  2.320093E+01
   496 |    45632 |  2.324103E+01
   497 |    45724 |  2.328091E+01
   498 |    45816 |  2.331116E+01
   499 |    45908 |  2.335107E+01
   500 |    46000 |  2.338091E+01
   501 |    46092 |  2.342089E+01
   502 |    46184 |  2.346090E+01
   503 |    46276 |  2.350578E+01
   504 |    46368 |  2.354083E+01
   505 |    46460 |  2.358080E+01
   506 |    46552 |  2.361885E+01
   507 |    46644 |  2.365587E+01
   508 |    46736 |  2.368607E+01
   509 |    46828 |  2.373096E+01
   510 |    46

   725 |    66700 |  3.297098E+01
   726 |    66792 |  3.301110E+01
   727 |    66884 |  3.305089E+01
   728 |    66976 |  3.310101E+01
   729 |    67068 |  3.314110E+01
   730 |    67160 |  3.319099E+01
   731 |    67252 |  3.323079E+01
   732 |    67344 |  3.326080E+01
   733 |    67436 |  3.330095E+01
   734 |    67528 |  3.335104E+01
   735 |    67620 |  3.339573E+01
   736 |    67712 |  3.343099E+01
   737 |    67804 |  3.347081E+01
   738 |    67896 |  3.351094E+01
   739 |    67988 |  3.355614E+01
   740 |    68080 |  3.360083E+01
   741 |    68172 |  3.365073E+01
   742 |    68264 |  3.369094E+01
   743 |    68356 |  3.373081E+01
   744 |    68448 |  3.378083E+01
   745 |    68540 |  3.381092E+01
   746 |    68632 |  3.385099E+01
   747 |    68724 |  3.390091E+01
   748 |    68816 |  3.395077E+01
   749 |    68908 |  3.398089E+01
   750 |    69000 |  3.403094E+01
   751 |    69092 |  3.406079E+01
   752 |    69184 |  3.410102E+01
   753 |    69276 |  3.415084E+01
   754 |    69

   966 |    88872 |  4.346079E+01
   967 |    88964 |  4.351604E+01
   968 |    89056 |  4.357611E+01
   969 |    89148 |  4.363087E+01
   970 |    89240 |  4.367069E+01
   971 |    89332 |  4.371579E+01
   972 |    89424 |  4.376109E+01
   973 |    89516 |  4.379113E+01
   974 |    89608 |  4.383080E+01
   975 |    89700 |  4.386082E+01
   976 |    89792 |  4.390104E+01
   977 |    89884 |  4.394111E+01
   978 |    89976 |  4.398082E+01
   979 |    90068 |  4.402084E+01
   980 |    90160 |  4.405076E+01
   981 |    90252 |  4.409582E+01
   982 |    90344 |  4.414569E+01
   983 |    90436 |  4.420104E+01
   984 |    90528 |  4.425101E+01
   985 |    90620 |  4.429098E+01
   986 |    90712 |  4.433575E+01
   987 |    90804 |  4.437092E+01
   988 |    90896 |  4.441091E+01
   989 |    90988 |  4.445066E+01
   990 |    91080 |  4.449091E+01
   991 |    91172 |  4.453688E+01
   992 |    91264 |  4.457076E+01
   993 |    91356 |  4.461075E+01
   994 |    91448 |  4.464097E+01
   995 |    91

...

  3805 |   350060 |  1.630515E+02
  3806 |   350152 |  1.630875E+02
  3807 |   350244 |  1.631305E+02
  3808 |   350336 |  1.631665E+02
  3809 |   350428 |  1.632119E+02
  3810 |   350520 |  1.632479E+02
  3811 |   350612 |  1.632839E+02
  3812 |   350704 |  1.633104E+02
  3813 |   350796 |  1.633425E+02
  3814 |   350888 |  1.633705E+02
  3815 |   350980 |  1.634024E+02
  3816 |   351072 |  1.634320E+02
  3817 |   351164 |  1.634640E+02
  3818 |   351256 |  1.634920E+02
  3819 |   351348 |  1.635268E+02
  3820 |   351440 |  1.635627E+02
  3821 |   351532 |  1.635987E+02
  3822 |   351624 |  1.636308E+02
  3823 |   351716 |  1.636627E+02
  3824 |   351808 |  1.637036E+02
  3825 |   351900 |  1.637716E+02
  3826 |   351992 |  1.638546E+02
  3827 |   352084 |  1.638986E+02
  3828 |   352176 |  1.639346E+02
  3829 |   352268 |  1.639746E+02
  3830 |   352360 |  1.640107E+02
  3831 |   352452 |  1.640467E+02
  3832 |   352544 |  1.640867E+02
  3833 |   352636 |  1.641267E+02
  3834 |   352

  4047 |   372324 |  1.725337E+02
  4048 |   372416 |  1.725740E+02
  4049 |   372508 |  1.726037E+02
  4050 |   372600 |  1.726537E+02
  4051 |   372692 |  1.726835E+02
  4052 |   372784 |  1.727138E+02
  4053 |   372876 |  1.727439E+02
  4054 |   372968 |  1.727839E+02
  4055 |   373060 |  1.728137E+02
  4056 |   373152 |  1.728537E+02
  4057 |   373244 |  1.728843E+02
  4058 |   373336 |  1.729339E+02
  4059 |   373428 |  1.729739E+02
  4060 |   373520 |  1.730188E+02
  4061 |   373612 |  1.730636E+02
  4062 |   373704 |  1.731038E+02
  4063 |   373796 |  1.731440E+02
  4064 |   373888 |  1.731839E+02
  4065 |   373980 |  1.732237E+02
  4066 |   374072 |  1.732535E+02
  4067 |   374164 |  1.732837E+02
  4068 |   374256 |  1.733139E+02
  4069 |   374348 |  1.733439E+02
  4070 |   374440 |  1.733737E+02
  4071 |   374532 |  1.734336E+02
  4072 |   374624 |  1.734638E+02
  4073 |   374716 |  1.735038E+02
  4074 |   374808 |  1.735336E+02
  4075 |   374900 |  1.735638E+02
  4076 |   374

  4289 |   394588 |  1.820498E+02
  4290 |   394680 |  1.820778E+02
  4291 |   394772 |  1.821098E+02
  4292 |   394864 |  1.821378E+02
  4293 |   394956 |  1.821699E+02
  4294 |   395048 |  1.822018E+02
  4295 |   395140 |  1.822338E+02
  4296 |   395232 |  1.822698E+02
  4297 |   395324 |  1.823018E+02
  4298 |   395416 |  1.823338E+02
  4299 |   395508 |  1.823658E+02
  4300 |   395600 |  1.824018E+02
  4301 |   395692 |  1.824338E+02
  4302 |   395784 |  1.824658E+02
  4303 |   395876 |  1.824978E+02
  4304 |   395968 |  1.825298E+02
  4305 |   396060 |  1.825698E+02
  4306 |   396152 |  1.825978E+02
  4307 |   396244 |  1.826298E+02
  4308 |   396336 |  1.826618E+02
  4309 |   396428 |  1.826899E+02
  4310 |   396520 |  1.827218E+02
  4311 |   396612 |  1.827552E+02
  4312 |   396704 |  1.827872E+02
  4313 |   396796 |  1.828152E+02
  4314 |   396888 |  1.828472E+02
  4315 |   396980 |  1.828794E+02
  4316 |   397072 |  1.829114E+02
  4317 |   397164 |  1.829434E+02
  4318 |   397

  4532 |   416944 |  1.902972E+02
  4533 |   417036 |  1.903293E+02
  4534 |   417128 |  1.903573E+02
  4535 |   417220 |  1.903893E+02
  4536 |   417312 |  1.904172E+02
  4537 |   417404 |  1.904491E+02
  4538 |   417496 |  1.904811E+02
  4539 |   417588 |  1.905133E+02
  4540 |   417680 |  1.905493E+02
  4541 |   417772 |  1.905867E+02
  4542 |   417864 |  1.906299E+02
  4543 |   417956 |  1.906660E+02
  4544 |   418048 |  1.907012E+02
  4545 |   418140 |  1.907412E+02
  4546 |   418232 |  1.907772E+02
  4547 |   418324 |  1.908173E+02
  4548 |   418416 |  1.908533E+02
  4549 |   418508 |  1.908973E+02
  4550 |   418600 |  1.909373E+02
  4551 |   418692 |  1.909733E+02
  4552 |   418784 |  1.910118E+02
  4553 |   418876 |  1.910438E+02
  4554 |   418968 |  1.910798E+02
  4555 |   419060 |  1.911175E+02
  4556 |   419152 |  1.911575E+02
  4557 |   419244 |  1.911935E+02
  4558 |   419336 |  1.912338E+02
  4559 |   419428 |  1.912778E+02
  4560 |   419520 |  1.913137E+02
  4561 |   419

  4779 |   439668 |  1.987209E+02
  4780 |   439760 |  1.987536E+02
  4781 |   439852 |  1.987819E+02
  4782 |   439944 |  1.988168E+02
  4783 |   440036 |  1.988417E+02
  4784 |   440128 |  1.988767E+02
  4785 |   440220 |  1.989128E+02
  4786 |   440312 |  1.989420E+02
  4787 |   440404 |  1.989770E+02
  4788 |   440496 |  1.990086E+02
  4789 |   440588 |  1.990388E+02
  4790 |   440680 |  1.990685E+02
  4791 |   440772 |  1.990988E+02
  4792 |   440864 |  1.991284E+02
  4793 |   440956 |  1.991617E+02
  4794 |   441048 |  1.991897E+02
  4795 |   441140 |  1.992287E+02
  4796 |   441232 |  1.992621E+02
  4797 |   441324 |  1.992887E+02
  4798 |   441416 |  1.993187E+02
  4799 |   441508 |  1.993517E+02
  4800 |   441600 |  1.993796E+02
  4801 |   441692 |  1.994137E+02
  4802 |   441784 |  1.994419E+02
  4803 |   441876 |  1.994768E+02
  4804 |   441968 |  1.995131E+02
  4805 |   442060 |  1.995486E+02
  4806 |   442152 |  1.995836E+02
  4807 |   442244 |  1.996285E+02
  4808 |   442